In [1]:
import requests
import re
import pandas as pd

In [2]:
url="http://finance.jxufe.edu.cn/news-list-fujiaoshou.html" #第一页副教授
url2="http://finance.jxufe.edu.cn/news-list-fujiaoshou-2.html" #第二页副教授

In [3]:
#定义函数截取第一页副教授的个人网站
def get_teachers_href(url):
    r=requests.get(url)
    r.encoding='utf-8'
    html_text=r.text
    searchObj_s=re.findall(r'<div class="textlist">.*?</div>',html_text)
    links_teacher={}
    for item in searchObj_s:
        name = item[81:-10]
        web=item[32:79]
        name = name.replace(' ', '')
        links_teacher[name]=web
    return(links_teacher) 

In [4]:
#定义函数清理自我简介和科研成果中的多余代码
def clear_tags(html_text):
    p = re.compile('<.*?>')
    text=''
    remaining_text = html_text
    searchObj = p.search(remaining_text)
    while searchObj is not None:
        text += remaining_text[:searchObj.start()]
        remaining_text = remaining_text[searchObj.end():]
        searchObj = p.search(remaining_text)
    return(text)

In [5]:
#定义函数获取网页中的基本信息
def get_value(key,html):
    pattern ='%s.*?：(.*?)</p>' % key
    searchObj=re.search(pattern,text)
    value=searchObj.group(1)
    return(value)

In [6]:
#定义函数返回基本信息
def parse_content(html):
    zzmm = get_value('政治面貌',html)
    zzmm = zzmm.replace('</span>','')
    zzmm = zzmm.replace('</strong>','')
    byyx=get_value('毕业院校',html)
    byyx = byyx.replace('</span>','')
    byyx = byyx.replace('</strong>','')
    byzy=get_value('毕业专业',html)
    byzy = byzy.replace('</span>','')
    byzy = byzy.replace('</strong>','')
    return((zzmm,byyx,byzy))

In [7]:
#获取两页的副教授的个人网站并合并在一个dataframe中
links=get_teachers_href(url)
links2=get_teachers_href(url2)
df=pd.DataFrame([links]).T
df2=pd.DataFrame([links2]).T
df=df.append(df2)

In [8]:
#设置df的列属性和索引，方便之后查看
df.columns=['个人网站']
df['姓名']=df.index
df=df.drop(['杜江泽','BadarNadeemAshraf','谭英贤','王金佑','赵玉洁']) #除去一些格式不一样的副教授的信息
df.reset_index(inplace=True,drop=True)
df['政治面貌']=''
df['毕业院校']=''
df['毕业专业']=''
df['自我简介']=''
df['科研成果']=''

In [9]:
#对剩下13个网页格式一样的副教授的信息进行爬取
for i in range (13):
    url3=df.iloc[i,0]
    message=requests.get(url3)
    message.encoding='utf-8'
    text=message.text
    #用定义的函数parse_content爬取到大家共有的基本信息：政治面貌，毕业院校和毕业专业
    jbxx=parse_content(text)
    #将值赋给每一位老师处
    df.loc[i,'政治面貌']=jbxx[0]
    df.loc[i,'毕业院校']=jbxx[1]
    df.loc[i,'毕业专业']=jbxx[2]
    #下面是截取自我简介和科研成果
    start_index = text.find('自我简介</span>')
    end_index = text.find('科研成果</span>')
    zwjj = text[start_index:end_index]
    zwjj_text = clear_tags(zwjj)
    #得到文本后对文本进行清洗
    zwjj_text=zwjj_text.replace('自我简介','')
    zwjj_text=zwjj_text.replace('&nbsp;','')
    #科研成果和自我简介的格式一致
    start_index2 = text.find('科研成果</span>')
    end_index2 = text.find('版权所有</a>')
    kycg = text[start_index2:end_index2]
    kycg_text = clear_tags(kycg)
    kycg_text=kycg_text.replace('科研成果','')
    kycg_text=kycg_text.replace('&nbsp;','')
    kycg_text=kycg_text.replace('\n','')
    #最终将自我简介和科研成果赋给每一位老师处
    df.loc[i,['自我简介']]=zwjj_text
    df.loc[i,['科研成果']]=kycg_text

In [10]:
print('最终信息提取结果：')
display(df)

最终信息提取结果：


个人网站   姓名     政治面貌        毕业院校  \
0   http://finance.jxufe.edu.cn/news-show-2073.html  胡少勇     中共党员      华东师范大学   
1   http://finance.jxufe.edu.cn/news-show-1300.html  胡志军     中共党员      上海财经大学   
2   http://finance.jxufe.edu.cn/news-show-1378.html   李英       群众      东北财经大学   
3   http://finance.jxufe.edu.cn/news-show-1379.html  李思敏     中共党员               
4   http://finance.jxufe.edu.cn/news-show-1376.html  闵晓平  中国民主促进会      上海交通大学   
5   http://finance.jxufe.edu.cn/news-show-2751.html   潜力           西安交通大学<br>   
6   http://finance.jxufe.edu.cn/news-show-1375.html  舒海棠     中共党员      江西财经大学   
7   http://finance.jxufe.edu.cn/news-show-1374.html  吴伟军     中共党员      江西财经大学   
8   http://finance.jxufe.edu.cn/news-show-3088.html  徐海云     中共党员    中南财经政法大学   
9   http://finance.jxufe.edu.cn/news-show-1368.html  钟小林     中共党员      江西财经大学   
10  http://finance.jxufe.edu.cn/news-show-1370.html  曾鸿志       党员        天津大学   
11  http://finance.jxufe.edu.cn/news-show-1367.html  曾莉华       群众      江西财经大学   
12  http://finance.jxufe.edu.cn/news-show-1369.html  邹朋飞       群众        暨南大学   

       毕业专业                                               自我简介  \
0       精算学  胡少勇 1979年7月生，汉族，江西进贤人，2012年博士毕业于华东师范大学金融统计学院精算...   
1     数量经济学  教育背景2009.09–2013.06就读于上海财经大学经济学院数量经济学专业，获经济学博士...   
2       金融学                                  、开设课程二、获得奖励三、社会兼职   
3             李思敏，男， 1968年9月生，1992年参加工作，1995年加入中国共产党，现任江西财大...   
4   管理科学与工程      研究主题：金融工程与风险管理关注基于人工智能的资产定价；公司金融理论与政策关注基于人...   
5       金融学  　　一、基本情况潜力：江西财经大学，内聘教授、硕导。主要从事资本结构、动态资产定价及金融大数...   
6       金融学  一、开设课程: 《货币银行学》、《金融监管》、《国际金融》、《金融理论与实务》、《银行信贷管...   
7       经济学  一、开设课程：公司金融、货币银行学、商业银行管理、投资学、信托与租赁。 二、获得奖励：201...   
8       统计学  徐海云：2010年6月毕业于中南财经政法大学统计与数学学院统计学专业，获经济学博士学位。20...   
9       金融学  一、开设课程《证券投资技术分析》、《证券投资基金》、《证券投资学》等。二、获得奖励2010年...   
10  投资经济管理学  一、开设课程：《公司金融》双语、《项目融资》二、获得奖励：2011年获“金牌教师”称号；三、...   
11  投资经济管理学  一、开设课程：《货币银行学》、《国际金融》、《中央银行学》、《国际金融实务》、《国际结算》二...   
12      金融学  校级骨干教师、金融发展与风险防范专职研究员开设课程：货币银行学、商业银行管理、金融计量学、固...   

                                                 科研成果  
0   五、发表的主要论文：1. Shaoyong Hu,Ailin Zhu,2016.Risk-M...  
1   论文：[16]Hu Z, Sun P-W. Connectedness among stoc...  
2                                                 ...  
3                                                 ...  
4     一、论文​(1)闵晓平. 随机动态环境下的公司债券流动性溢价影响因素研究. 浙江金融. ...  
5   1. 发表的主要论文：[1]. 潜力、胡援成“经济周期、融资约束与资本结构的非线性调整”,《...  
6   一、论文1．《试析我国商业银行信用风险控制》，独著，《金融与经济》 2006(12)；2．《...  
7   一、学术论文[1]吴伟军，转轨时期中国货币政策传导机制有效性的实证研究, [J]《江西社会科...  
8   研究成果 [1]Xu Haiyun.Linear and nonlinear causali...  
9   一、论文1.“浅析指数基金的指数化投资方法”，独著，《证券市场导报》2003年第2期。2.“...  
10  一、论文1．曾鸿志，货币调整、资本市场与实体部门的长期互动,《中国经济问题》，2011（2）...  
11  一、论文1.“基于银行电子化发展的高校银行实验模拟教学系统设计“，独著，《电化教育研究》，2...  
12  发表的主要论文：1.银行信贷、房地产价格与实际产出关系的经验研究,独著,2008-12,山西...